# Deliverable 3. Create a Travel Itinerary Map

----

1. Create a folder called `Vacation_Itinerary` to store all the files for this deliverable.

2. Download the `Vacation_Itinerary_starter_code.ipynb` file into your `Vacation_Itinerary` folder and rename it `Vacation_Itinerary.ipynb`.

3. Make sure the initial dependencies and the Geoapify API key are imported.

4. From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`.

5. Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

    * The point's size should be the maximum temperature for the city

    * The point's color should be the city's name

    * Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

6. From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

    > **Hint:** You will start and end the route in the same city, so the `vacation_start` and `vacation_end` DataFrames will be in the same city.

7. Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details.

8. Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`.

    > **Hint:** You'll use this DataFrame to create a map using GeoViews, so recall that the first column should be the longitude, and the second the latitude.

9. Use GeoViews to create a map that shows the four cities in the itinerary.

10. Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop.

    > **Hint:** You can note that the `mode` parameter is set to `drive`, you can play around with other modes as it's shown in [the "Travel modes" table](https://apidocs.geoapify.com/docs/routing/#api) in the Geoapify Routing API documentation.

11. Use the Geoapify Routing API to retrieve the route's directions for your itinerary.

12. From the JSON response, store the route's legs coordinates in a variable called `legs`.

13. Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude values into two Python lists named `longitude` and `latitude`.

14. Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`.

15. Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map.

16. Use the asterisk operator to display a composed plot that shows the itinerary's route over the map containing the cities. 

17. Save your map to the `Vacation_Itinerary` folder as `WeatherPy_travel_map.png`.

---

## Make sure the initial dependencies and the Geoapify API key are imported

In [1]:
# Dependencies and Setup
import geoviews as gv
import hvplot.pandas
import pandas as pd
import requests

# Turn off warning messages
import warnings
warnings.filterwarnings("ignore")

# Import API key
from config import GAPI_key

## From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`

In [2]:
# Read the WeatherPy_vacation.csv into a DataFrame
vacation_df = pd.read_csv("WeatherPy_vacation.csv")

# Display sample data
vacation_df.head()

City ID            City Country  Max Temp Current Description      Lat  \
0        0           Vaini      TO     80.76    scattered clouds -21.2000   
1        1           Tabou      CI     79.45       moderate rain   4.4230   
2       12         Huarmey      PE     77.88     overcast clouds -10.0681   
3       13    Vila Do Maio      CV     75.99       broken clouds  15.1333   
4       18  Saint-Philippe      RE     80.19     overcast clouds -21.3585   

        Lng                   Hotel Name  
0 -175.2000  Keleti International Resort  
1   -7.3528              hôtel le rochet  
2  -78.1522            Hostal Santa Rosa  
3  -23.2167  Residencial Jardins De Maio  
4   55.7679                     Le Baril

## Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

* The point's size should be the maximum temperature for the city

* The point's color should be the city's name

* Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

In [3]:
# Configure the map plot
map_plot = vacation_df.hvplot.points("Lng","Lat",
                                        geo=True, tiles="OSM", frame_width= 700,
                                          frame_height = 500, size = "Max Temp", scale = 0.5, color = "City",hover_cols = ["Hotel Name","Country","Current Description"])


# Display the map
map_plot

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp,Hotel Name,Country,Current Description)

## From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

In [33]:
df = vacation_df.loc[vacation_df["Country"]=="US"]
df.head(10)


City ID                City Country  Max Temp      Current Description  \
9         41               Kapaa      US     78.12               few clouds   
10        46                Hilo      US     79.29                clear sky   
47       172         Terre Haute      US     73.06                clear sky   
62       248       Makakilo City      US     76.69  light intensity drizzle   
63       251            Hamilton      US     75.15                clear sky   
84       335          Wilmington      US     71.94                clear sky   
100      394         San Antonio      US     81.99            broken clouds   
104      410  Hilton Head Island      US     78.91                clear sky   
119      488           Knoxville      US     77.25                clear sky   
124      523        Fort Stewart      US     84.29         scattered clouds   

         Lat       Lng                                  Hotel Name  
9    22.0752 -159.3190                             Pono Kai Resort  
10   19.7297 -155.0900                           Dolphin Bay Hotel  
47   39.4667  -87.4139                                  Travelodge  
62   21.3469 -158.0858       Embassy Suites by Hilton Oahu Kapolei  
63   39.1834  -84.5333                           North Vista Manor  
84   34.2257  -77.9447                              Hell's Kitchen  
100  29.4241  -98.4936            Riverwalk Plaza Hotel and Suites  
104  32.2163  -80.7526  Marriott's Harbour Point and Sunset Pointe  
119  35.9606  -83.9207                            Hilton Knoxville  
124  31.8722  -81.6100                  IHG Army Hotels Main Lodge

In [34]:
# Create DataFrames for each city by filtering the 'vacation_df' using the loc method
vacation_start = vacation_df.loc[vacation_df["City"]=="Fort Stewart"]
vacation_end = vacation_df.loc[vacation_df["City"]=="Wilmington"]
vacation_stop1 =vacation_df.loc[vacation_df["City"]=="Knoxville"] 
vacation_stop2 =vacation_df.loc[vacation_df["City"]=="Hamilton"] 
vacation_stop3 =vacation_df.loc[vacation_df["City"]=="San Antonio"] 

## Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details

In [35]:
# Use the Pandas concat function to create a new DataFrame to store the itinerary details.
frames=[vacation_start,vacation_stop1,vacation_stop2,vacation_stop3,vacation_end]
itinerary_df = pd.concat(frames)

# Display sample data
itinerary_df.head()

City ID          City Country  Max Temp Current Description      Lat  \
124      523  Fort Stewart      US     84.29    scattered clouds  31.8722   
119      488     Knoxville      US     77.25           clear sky  35.9606   
63       251      Hamilton      US     75.15           clear sky  39.1834   
100      394   San Antonio      US     81.99       broken clouds  29.4241   
84       335    Wilmington      US     71.94           clear sky  34.2257   

         Lng                        Hotel Name  
124 -81.6100        IHG Army Hotels Main Lodge  
119 -83.9207                  Hilton Knoxville  
63  -84.5333                 North Vista Manor  
100 -98.4936  Riverwalk Plaza Hotel and Suites  
84  -77.9447                    Hell's Kitchen

## Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`

In [36]:
# Create a Pandas DataFrame to store the latitude and longitude for each city in the itineray
waypoints_df = itinerary_df[["Lng","Lat"]].copy()

# Display sample data
waypoints_df.head()

Lng      Lat
124 -81.6100  31.8722
119 -83.9207  35.9606
63  -84.5333  39.1834
100 -98.4936  29.4241
84  -77.9447  34.2257

## Use GeoViews to create map that shows the four cities in the itinerary

In [37]:
# Configure the map plot by using the itineraty_df
waypoints_map = itinerary_df.hvplot.points("Lng","Lat",
                                        geo=True, tiles="OSM", frame_width= 700,
                                          frame_height = 500, size = "Max Temp", scale =2, color = "City",hover_cols = ["Hotel Name","Country","Current Description"])



In [38]:
# Display the route_map
waypoints_map

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp,Hotel Name,Country,Current Description)

## Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop

In [39]:
# Set parameters to trace the route
radius = 5000
params = {
    "mode":"drive",
    "apiKey": GAPI_key,
}

In [40]:
# Set an empty waypoints String variable
waypoints = ""

# Iterate through the route_df DataFrame to define the waypoints
for index, row in waypoints_df.iterrows():
    waypoints = waypoints + str(row["Lat"]) + "," + str(row["Lng"]) + "|"

# Delete the last character from the string
waypoints = waypoints[:-1]

# Add the waypoints to the params dictionary
params["waypoints"] = waypoints

# Display the params dictionary
params

{'mode': 'drive',
 'apiKey': 'a455648782b844c6ad0a2b30a4a50c4f',
 'waypoints': '31.8722,-81.61|35.9606,-83.9207|39.1834,-84.5333|29.4241,-98.4936|34.2257,-77.9447'}

## Use the Geoapify Routing API to retrieve the route's directions for your itinerary

In [41]:
# Set up the base URL for the Geoapify Places API.
base_url = "https://api.geoapify.com/v1/routing"

# Make request and retrieve the JSON data by using the params dictionaty
route_response = requests.get(base_url,params=params)

# Convert the API response to JSON format
route_response = route_response.json()




In [42]:
route_response

{'features': [{'type': 'Feature',
   'properties': {'mode': 'drive',
    'waypoints': [{'location': [-81.61, 31.8722], 'original_index': 0},
     {'location': [-83.9207, 35.9606], 'original_index': 1},
     {'location': [-84.5333, 39.1834], 'original_index': 2},
     {'location': [-98.4936, 29.4241], 'original_index': 3},
     {'location': [-77.9447, 34.2257], 'original_index': 4}],
    'units': 'metric',
    'distance': 5388156,
    'distance_units': 'meters',
    'time': 176146.99,
    'legs': [{'distance': 722686,
      'time': 24829.976,
      'steps': [{'from_index': 0,
        'to_index': 1,
        'distance': 63,
        'time': 6.522,
        'instruction': {'text': 'Drive northeast on West 5th Street North.'}},
       {'from_index': 1,
        'to_index': 52,
        'distance': 2919,
        'time': 300.716,
        'instruction': {'text': 'Bear left onto Hero Road.'}},
       {'from_index': 52,
        'to_index': 65,
        'distance': 61,
        'time': 12.544,
        

## From the JSON response, store the route's legs coordinates in a variable called `legs`

In [43]:
# Fetch the route's legs coordinates from the JSON reponse
legs = route_response["features"][0]["geometry"]["coordinates"]

## Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude value into two Python lists names `longitude` and `latitude`

In [44]:
# Create and empty list to store the longitude of each step
longitude = []

# Create and empty list to store the latitude of step
latitude = []

# Loop through the legs coordinates to fetch the latitude and longitude for each step
for leg in legs:
    for coordinate in leg:
        longitude.append(coordinate[0])
        latitude.append(coordinate[1])

## Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`

In [45]:
# Create an empty DataFrame to store the steps' coordinates
route_df = pd.DataFrame()

# Add the steps' longitude and latitude from each step as columns to the DataFrame
route_df["longitude"] = longitude
route_df["latitude"] = latitude

# Display sample data
route_df.head()

longitude   latitude
0 -81.610095  31.872284
1 -81.609608  31.872680
2 -81.609597  31.872908
3 -81.609566  31.873492
4 -81.609553  31.873747

##  Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map

In [46]:
# Configure the route path by using the GeoViews' Path function
route_path = gv.Path(
    route_df,
).opts(
    height=500,
    width=700,
    line_width = 3,
    color = "blue"
)

In [47]:
# Display a composed plot by using the route_map and route_path objects
waypoints_map*route_path

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp,Hotel Name,Country,Current Description)
   .Path.I   :Path   [longitude,latitude]